<a href="https://colab.research.google.com/github/wabinyai/Mapping-with-Folium-/blob/main/%5B12_03_2022_How_to_draw_a_variety_of_maps_with_folium_in_python.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
pip install geopandas

     |████████████████████████████████| 1.0 MB 2.4 MB/s 
     |████████████████████████████████| 16.7 MB 188 kB/s 
     |████████████████████████████████| 6.3 MB 33.6 MB/s 


In [3]:
pip install iteration_utilities

     |████████████████████████████████| 283 kB 2.7 MB/s 


In [4]:
import pandas as pd
import geopandas as gpd
import folium
import branca.colormap as cm
import matplotlib.pyplot as plt
from iteration_utilities import duplicates
from google.colab import files
from folium.plugins import FastMarkerCluster

# Datasets

**Air Quality data**

In [5]:
uploaded = files.upload()

for fn in uploaded.keys():
  print('User uploaded file "{name}" with length {length} bytes'.format(
      name=fn, length=len(uploaded[fn])))

Saving Garages_gps_location.csv to Garages_gps_location.csv
User uploaded file "Garages_gps_location.csv" with length 370 bytes


In [6]:
listing_df = pd.read_csv(fn)
listing_df.head(10)

parish  latitude  longitude Name  Vehicle
0    Wabigalo  0.313991  32.604819    a       12
1      Kisugu  0.311347  32.604967    b       45
2    Wabigalo  0.311917  32.605092    c       63
3      Kibuli  0.308583  32.597411    d       74
4      Kibuli  0.308292  32.597281    e       25
5      Kisugu  0.311137  32.608640    f       14
6      Kisugu  0.310886  32.604814    g       98
7  Kabalagala  0.299045  32.599439    h       35
8    Wabigalo  0.310909  32.602309    i      120
9      Kisugu  0.310539  32.604756    j       78

# Kampala Parish 

In [7]:
uploaded = files.upload()

for fn1 in uploaded.keys():
  print('User uploaded file "{name}" with length {length} bytes'.format(
      name=fn1, length=len(uploaded[fn1])))

Saving Kla.json to Kla.json
User uploaded file "Kla.json" with length 345171 bytes


In [8]:
fname = fn1
nbh_geo_df = gpd.read_file(fname)
nbh_geo_df.head()

id           UBOS_PN_13           UBOS_PN_06 UBOS_SN_13 UBOS_SN_06  \
0  None                Ggaba                Ggaba   MAKINDYE   Makindye   
1  None               Luzira               Luzira     NAKAWA     Nakawa   
2  None               Rubaga               Rubaga     RUBAGA     Rubaga   
3  None         Civic Centre         Civic Centre    CENTRAL    Central   
4  None  Makerere University  Makerere University    KAWEMPE    Kawempe   

  UBOS_DN_12  Male2002  Female2002  Total2002  Male2012  ...  Total2012  \
0    KAMPALA      9605       10607      20212     13900  ...      29400   
1    KAMPALA      7355        8071      15426     10600  ...      22400   
2    KAMPALA      9284       11423      20707     13600  ...      30300   
3    KAMPALA       645         562       1207      1000  ...       1900   
4    KAMPALA      2389        2262       4651      3400  ...       6700   

      Total2013   PopDensity    Shape_Leng    Shape_Area  created_us  \
0  30408.337430  4391.119070  18522.619313  6.695332e+06        None   
1  23182.303210  6512.657693  14850.056790  3.439456e+06        None   
2  31397.166310  9072.882488   7845.823752  3.339622e+06        None   
3   1935.834785  1572.890739   5666.401709  1.207967e+06        None   
4   6976.106971  5552.764196   4637.684949  1.206606e+06        None   

  created_da last_edite last_edi_1  \
0       None       None       None   
1       None       None       None   
2       None       None       None   
3       None       None       None   
4       None       None       None   

                                            geometry  
0  MULTIPOLYGON (((32.65672 0.27464, 32.65677 0.2...  
1  MULTIPOLYGON (((32.66630 0.29248, 32.66631 0.2...  
2  POLYGON ((32.55831 0.30785, 32.55848 0.30739, ...  
3  POLYGON ((32.59345 0.31752, 32.59342 0.31750, ...  
4  POLYGON ((32.57134 0.34083, 32.57147 0.34024, ...  

[5 rows x 21 columns]

In [9]:
nbh_geo_df = nbh_geo_df[['UBOS_PN_13', 'geometry']]
nbh_geo_df.head()

UBOS_PN_13                                           geometry
0                Ggaba  MULTIPOLYGON (((32.65672 0.27464, 32.65677 0.2...
1               Luzira  MULTIPOLYGON (((32.66630 0.29248, 32.66631 0.2...
2               Rubaga  POLYGON ((32.55831 0.30785, 32.55848 0.30739, ...
3         Civic Centre  POLYGON ((32.59345 0.31752, 32.59342 0.31750, ...
4  Makerere University  POLYGON ((32.57134 0.34083, 32.57147 0.34024, ...

In order to put points on the map, we need to convert each coordinate to geopoint, same for the dataframe.

In [10]:
from shapely.geometry import Point, shape

locs_geometry = [Point(xy) for xy in zip(listing_df.longitude,
                                         listing_df.latitude)]
crs = {'init': 'epsg:4326'}
# Coordinate Reference Systems, "epsg:4326" is a common projection of WGS84 Latitude/Longitude
locs_gdf = gpd.GeoDataFrame(listing_df, crs=crs, geometry=locs_geometry)

/usr/local/lib/python3.7/dist-packages/pyproj/crs/crs.py:131: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)


In [11]:
# Assigning centroids to the map
x_map=nbh_geo_df.centroid.x.mean()
y_map=nbh_geo_df.centroid.y.mean()
print(x_map,y_map)

32.588378452359045 0.32595425109652304


# Display all locations with points on the map

In [31]:
import folium
locs_map = folium.Map(location=[y_map, x_map],
                      zoom_start=13, tiles='cartodbpositron')

feature_ea = folium.FeatureGroup(name='Wabigalo')
feature_pr = folium.FeatureGroup(name='Kibuli')
feature_sr = folium.FeatureGroup(name='Kisugu')
feature_sr = folium.FeatureGroup(name='Kabalagala')
for i, v in locs_gdf.iterrows():
    popup = """
 
    parish : <b>%s</b><br>
    Vehicle : <b>%s</b><br>

    """ % ( v['parish'], v['Vehicle'])
    
    if v['parish'] == 'Wabigalo':
        folium.CircleMarker(location=[v['latitude'], v['longitude']],
                            radius=1,
                            tooltip=popup,
                            color='#FFBA00',
                            fill_color='#FFBA00',
                            fill=True).add_to(feature_ea)
    elif v['parish'] == 'Kibuli':
        folium.CircleMarker(location=[v['latitude'], v['longitude']],
                            radius=1,
                            tooltip=popup,
                            color='#087FBF',
                            fill_color='#087FBF',
                            fill=True).add_to(feature_pr)
    elif v['parish'] == 'Kisugu':
        folium.CircleMarker(location=[v['latitude'], v['longitude']],
                            radius=1,
                            tooltip=popup,
                            color='#087FBF',
                            fill_color='#087FBF',
                            fill=True).add_to(feature_pr)
    elif v['parish'] == 'Kabalagala':
        folium.CircleMarker(location=[v['latitude'], v['longitude']],
                            radius=1,
                            tooltip=popup,
                            color='#087FBF',
                            fill_color='#087FBF',
                            fill=True).add_to(feature_pr)
'''    elif v['room_type'] == 'Shared room':
        folium.CircleMarker(location=[v['latitude'], v['longitude']],
                            radius=1,
                            tooltip=popup,
                            color='#FF0700',
                            fill_color='#FF0700',
                            fill=True).add_to(feature_sr)
'''
feature_ea.add_to(locs_map)
feature_pr.add_to(locs_map)
#feature_sr.add_to(locs_map)
folium.LayerControl(collapsed=False).add_to(locs_map)

In [32]:
locs_map

# Display all locations with clusters

In [34]:
from folium import plugins

cluster_map = folium.Map(location=[y_map, x_map],
                      zoom_start=13, tiles='cartodbpositron')

marker_cluster = plugins.MarkerCluster().add_to(cluster_map)
for i, v in locs_gdf.iterrows():
    popup = """
 
    parish : <b>%s</b><br>
    Vehicle : <b>%s</b><br>

    """ % ( v['parish'], v['Vehicle'])
    
    if v['parish'] == 'Wabigalo':
        folium.CircleMarker(location=[v['latitude'], v['longitude']],
                            radius=3,
                            tooltip=popup,
                            color='#FFBA00',
                            fill_color='#FFBA00',
                            fill=True).add_to(marker_cluster)
    elif v['parish'] == 'Kibuli':
        folium.CircleMarker(location=[v['latitude'], v['longitude']],
                            radius=3,
                            tooltip=popup,
                            color='#087FBF',
                            fill_color='#087FBF',
                            fill=True).add_to(marker_cluster)
    elif v['parish'] == 'Kisugu':
        folium.CircleMarker(location=[v['latitude'], v['longitude']],
                            radius=3,
                            tooltip=popup,
                            color='#087FBF',
                            fill_color='#087FBF',
                            fill=True).add_to(marker_cluster)
    elif v['parish'] == 'Kabalagala':
        folium.CircleMarker(location=[v['latitude'], v['longitude']],
                            radius=3,
                            tooltip=popup,
                            color='#087FBF',
                            fill_color='#087FBF',
                            fill=True).add_to(marker_cluster)

cluster_map

# Paint areas with different colors

# Rename a column 

In [15]:
listing_df = listing_df.rename(columns={'parish': 'UBOS_PN_13'})
listing_df.head()

UBOS_PN_13  latitude  longitude Name  Vehicle                  geometry
0   Wabigalo  0.313991  32.604819    a       12  POINT (32.60482 0.31399)
1     Kisugu  0.311347  32.604967    b       45  POINT (32.60497 0.31135)
2   Wabigalo  0.311917  32.605092    c       63  POINT (32.60509 0.31192)
3     Kibuli  0.308583  32.597411    d       74  POINT (32.59741 0.30858)
4     Kibuli  0.308292  32.597281    e       25  POINT (32.59728 0.30829)

# Paint areas with different colors

In [61]:
nbh_count_df = listing_df.groupby('UBOS_PN_13')['Vehicle'].nunique().reset_index()
nbh_count_df.rename(columns={'Vehicle':'nb'}, inplace=True)
nbh_geo_count_df = pd.merge(nbh_geo_df, nbh_count_df, on='UBOS_PN_13')
nbh_geo_count_df['QP'] = nbh_geo_count_df['nb'] / nbh_geo_count_df['nb'].sum()
nbh_geo_count_df['QP_str'] = nbh_geo_count_df['QP'].apply(lambda x : str(round(x*100, 1)) + '%')

from branca.colormap import linear
nbh_count_colormap = linear.YlGnBu_09.scale(min(nbh_count_df['nb']),
                                            max(nbh_count_df['nb']))

nbh_locs_map = folium.Map(location=[y_map, x_map],
                          zoom_start = 12)

#ADDING KAMPALA PARISH BOUNDARIES

#Adding ALL boundaries of Kampala parishes

nbh_geo_df.crs = "epsg:4326"

folium.Choropleth(geo_data=nbh_geo_df,
                    name="choropleth",

                      fill_opacity=0.1,
                     line_opacity=0.3,
                     ).add_to(nbh_locs_map)

#######################


style_function = lambda x: {
    'fillColor': nbh_count_colormap(x['properties']['nb']),
    'color': 'black',
    'weight': 1.5,
    'fillOpacity': 0.7
}

crs = {'init': 'epsg:4326'}
# Coordinate Reference Systems, "epsg:4326" is a common projection of WGS84 Latitude/Longitude
#locs_gdf = gpd.GeoDataFrame(listing_df, crs=crs, geometry=locs_geometry)

nbh_geo_count_df.crs = "epsg:4326"

folium.GeoJson(
    nbh_geo_count_df,
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(
        fields=['UBOS_PN_13', 'nb', 'QP_str'],
        aliases=['Parish', 'Location amount', 'Quote-part'],
        localize=True
    )
).add_to(nbh_locs_map)



nbh_count_colormap.add_to(nbh_locs_map)
nbh_count_colormap.caption = 'Garages location concentration amount'
nbh_count_colormap.add_to(nbh_locs_map)

In [62]:
nbh_locs_map

In [54]:
nbh_count_df = listing_df.groupby('UBOS_PN_13')['Vehicle'].nunique().reset_index()
nbh_count_df.rename(columns={'Vehicle':'nb'}, inplace=True)
nbh_geo_count_df = pd.merge(nbh_geo_df, nbh_count_df, on='UBOS_PN_13')
nbh_geo_count_df['QP'] = nbh_geo_count_df['nb'] / nbh_geo_count_df['nb'].sum()
nbh_geo_count_df['QP_str'] = nbh_geo_count_df['QP'].apply(lambda x : str(round(x*100, 1)) + '%')

from branca.colormap import linear
nbh_count_colormap = linear.YlGnBu_09.scale(min(nbh_count_df['nb']),
                                            max(nbh_count_df['nb']))

nbh_locs_map = folium.Map(location=[y_map, x_map],
                          zoom_start = 12)





#Adding ALL boundaries of Kampala parishes

nbh_geo_df.crs = "epsg:4326"

folium.Choropleth(geo_data=nbh_geo_df,
                    name="choropleth",

                      fill_opacity=0.1,
                     line_opacity=0.3,
                     ).add_to(nbh_locs_map)

# Labeling Parished withouth Auto safty afiliated Garage

######
#########

# Adding informative lables to the map using geoJson

style_function1 = lambda x: {'fillColor': '#ffffff', 
                            'color':'#000000', 
                            'fillOpacity': 0.2, 
                            'weight': 0.1}
highlight_function1 = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.20, 
                                'weight': 0.1}


#########
SuburbName1 = folium.features.GeoJson(
    nbh_geo_df,
    style_function=style_function1, 
    control=False,
    highlight_function=highlight_function1, 
    tooltip=folium.features.GeoJsonTooltip(
        fields=['UBOS_PN_13'
 #               ,'Vehicle'
 #               ,'UBOS_PN_13'
 #               ,'  Yearly average taxable income of Female   '
 #               ,'  Yearly average taxable income of Male   '
               ],
        aliases=['Parish ::'
 #               ,'Vehicle repaired :: '
 #               ,'CITY: '
 #               ,'  Yearly average taxable income of Female   : '
 #               ,'  Yearly average taxable income of Male   : ' 
                 ],
        style=("background-color: lightblue; color: #333333; font-family: arial; font-size: 12px; padding: 10px;") 
    )
)
nbh_locs_map.add_child(SuburbName1)
nbh_locs_map.keep_in_front(SuburbName1)

##############
#######################################
style_function = lambda x: {
    'fillColor': nbh_count_colormap(x['properties']['nb']),
    'color': 'black',
    'weight': 1.5,
    'fillOpacity': 0.9
}

crs = {'init': 'epsg:4326'}
# Coordinate Reference Systems, "epsg:4326" is a common projection of WGS84 Latitude/Longitude
#locs_gdf = gpd.GeoDataFrame(listing_df, crs=crs, geometry=locs_geometry)

nbh_geo_count_df.crs = "epsg:4326"

folium.GeoJson(
    nbh_geo_count_df,
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(
        fields=['UBOS_PN_13', 'nb', 'QP_str'],
        aliases=['Parish', 'Number of Garages', 'Percenga of garage: '],
        localize=True
    )
).add_to(nbh_locs_map)

nbh_count_colormap.add_to(nbh_locs_map)
nbh_count_colormap.caption = 'Garages location concentration amount'
nbh_count_colormap.add_to(nbh_locs_map)
nbh_locs_map